## Downloading data and Login with AIicrowd CLI

In [1]:
!pip install transformers aicrowd-cli wandb -q

     |████████████████████████████████| 2.5MB 39.5MB/s 
     |████████████████████████████████| 51kB 8.9MB/s 
     |████████████████████████████████| 1.8MB 19.5MB/s 
     |████████████████████████████████| 3.3MB 38.9MB/s 
     |████████████████████████████████| 901kB 39.6MB/s 
     |████████████████████████████████| 61kB 8.5MB/s 
     |████████████████████████████████| 215kB 54.2MB/s 
     |████████████████████████████████| 174kB 59.2MB/s 
     |████████████████████████████████| 133kB 60.0MB/s 
     |████████████████████████████████| 102kB 14.4MB/s 
     |████████████████████████████████| 51kB 7.9MB/s 
     |████████████████████████████████| 71kB 11.7MB/s 
ERROR: aicrowd-cli 0.1.7 has requirement requests<3,>=2.25.1, but you'll have requests 2.23.0 which is incompatible.
ERROR: aicrowd-cli 0.1.7 has requirement tqdm<5,>=4.56.0, but you'll have tqdm 4.41.1 which is incompatible.


In [2]:
!pip install simpletransformers

     |████████████████████████████████| 225kB 28.1MB/s 
     |████████████████████████████████| 245kB 37.6MB/s 
     |████████████████████████████████| 7.8MB 51.6MB/s 
     |████████████████████████████████| 1.2MB 41.6MB/s 
     |████████████████████████████████| 51kB 9.0MB/s 
     |████████████████████████████████| 122kB 55.5MB/s 
     |████████████████████████████████| 81kB 2.0MB/s 
     |████████████████████████████████| 122kB 50.3MB/s 
     |████████████████████████████████| 245kB 56.3MB/s 
     |████████████████████████████████| 4.2MB 53.6MB/s 
     |████████████████████████████████| 112kB 59.7MB/s 
     |████████████████████████████████| 81kB 11.8MB/s 
     |████████████████████████████████| 122kB 59.5MB/s 
  Created wheel for seqeval: filename=seqeval-1.2.2-cp37-none-any.whl size=16184 sha256=3d09b50ef231311761e6e5c6a8ad6d8cac32b764eacd626bdb4e51d860136399
  Stored in directory: /root/.cache/pip/wheels/52/df/1b/45d75646c37428f7e626214704a0e35bd3cfc32eda37e59e5f
  Created wheel f

API Key valid
Saved API Key successfully!


In [4]:
# Downloading the Dataset ( removing data and assets folder if existing already and then creating the folder )
!rm -rf data
!mkdir data
!rm -rf assets
!mkdir assets



test.csv:   0% 0.00/3.01M [00:00<?, ?B/s]
val.csv:   0% 0.00/883k [00:00<?, ?B/s]
val.csv: 100% 883k/883k [00:00<00:00, 2.55MB/s]

test.csv: 100% 3.01M/3.01M [00:00<00:00, 6.45MB/s]

train.csv: 100% 8.77M/8.77M [00:00<00:00, 8.87MB/s]


### Importing Libraries

In [5]:
from simpletransformers.classification import ClassificationModel
import numpy as np
import pandas as pd

In [18]:
import os

In [6]:
train_path = "/content/data/train.csv"
val_path = "/content/data/val.csv"
test_path = "/content/data/test.csv"

train_df = pd.read_csv(train_path)
val_df = pd.read_csv(val_path)
test_df = pd.read_csv(test_path)

In [7]:
train_df

id                                               text  label
0          0  we propose deep network models and learning al...      3
1          1  multi-distance information computed by the MDL...      3
2          2  traditional solutions consider dense pedestria...      2
3          3  in this paper, is used the lagrangian classica...      2
4          4  the aim of this work is to determine how vulne...      3
...      ...                                                ...    ...
31495  31495  the proposed method is easily programmed by ki...      2
31496  31496  research in unpaired video translation has foc...      3
31497  31497  deep learning models exhibit limited generaliz...      3
31498  31498  in this paper, we aim to incorporate global se...      3
31499  31499  to precisely calculate context-based probabili...      3

[31500 rows x 3 columns]

In [8]:
train_df['label'].value_counts()

3    19676
0     4352
1     4078
2     3394
Name: label, dtype: int64

In [9]:
combined_data = pd.concat([train_df,val_df],axis=0)

In [10]:
combined_data.drop(['id'],axis=1,inplace=True)

In [11]:
custom_args = {'fp16': True, # not using mixed precision 
               'train_batch_size': 16, # default is 8
               'gradient_accumulation_steps': 2,
               'do_lower_case': True,
               'learning_rate': 1e-05, # using lower learning rate
               'overwrite_output_dir': True, # important for CV
               'num_train_epochs': 2} # default is 1

In [12]:
model = ClassificationModel("roberta", "xlm-roberta-large", args=custom_args,num_labels=4) 
model.train_model(combined_data,)

Downloading:   0%|          | 0.00/513 [00:00<?, ?B/s]

You are using a model of type xlm-roberta to instantiate a model of type roberta. This is not supported for all configurations of models and can yield errors.


Downloading:   0%|          | 0.00/2.24G [00:00<?, ?B/s]

Some weights of the model checkpoint at xlm-roberta-large were not used when initializing RobertaForSequenceClassification: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.dense.weight', 'lm_head.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at xlm-roberta-large and are newly initialized: ['classifier.dense.bias', 'classifier.out_proj.weight', 'classifier.out_proj.bias', 'cla

Downloading:   0%|          | 0.00/9.10M [00:00<?, ?B/s]

...

Running Epoch 0 of 2:   0%|          | 0/2138 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/simpletransformers/classification/classification_model.py:927: FutureWarning: Non-finite norm encountered in torch.nn.utils.clip_grad_norm_; continuing anyway. Note that the default behavior will change in a future release to error out if a non-finite total norm is encountered. At that point, setting error_if_nonfinite=false will be required to retain the old behavior.
  model.parameters(), args.max_grad_norm


Running Epoch 1 of 2:   0%|          | 0/2138 [00:00<?, ?it/s]

Exception ignored in: <generator object tqdm.__iter__ at 0x7f7367f73ed0>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/tqdm/std.py", line 1193, in __iter__
    self.close()
  File "/usr/local/lib/python3.7/dist-packages/tqdm/notebook.py", line 283, in close
    self.disp(bar_style='danger', check_delay=False)
  File "/usr/local/lib/python3.7/dist-packages/tqdm/notebook.py", line 177, in display
    rtext.value = right
  File "/usr/local/lib/python3.7/dist-packages/traitlets/traitlets.py", line 604, in __set__
    self.set(obj, value)
  File "/usr/local/lib/python3.7/dist-packages/traitlets/traitlets.py", line 593, in set
    obj._notify_trait(self.name, old_value, new_value)
  File "/usr/local/lib/python3.7/dist-packages/traitlets/traitlets.py", line 1222, in _notify_trait
    type='change',
  File "/usr/local/lib/python3.7/dist-packages/ipywidgets/widgets/widget.py", line 605, in notify_change
    self.send_state(key=name)
  File "/usr/local/lib/pyt

KeyboardInterrupt: ignored

In [13]:
predictions, raw_outputs = model.predict(list(test_df['text'].values))

  0%|          | 0/10800 [00:00<?, ?it/s]

  0%|          | 0/1350 [00:00<?, ?it/s]

In [15]:
# Applying the predictions to the labels column of the sample submission 
test_df['label'] = predictions
test_df

id                                               text  label
0          0  we propose a lightweight framework to detect i...      3
1          1  the proposed method presents an alternate solu...      2
2          2  proposed ear identification method fusing SIFT...      3
3          3  a method to reconstruct the three-dimensional ...      3
4          4  strong local consistencies can improve their p...      0
...      ...                                                ...    ...
10795  10795  whole-body gradient echo scans of 240 subjects...      3
10796  10796  we present a tracker that accomplishes trackin...      3
10797  10797  the most popular FL algorithm is Federated Ave...      1
10798  10798  in the field of Autonomous Driving, the system...      2
10799  10799  our method takes as an input a foreground imag...      3

[10800 rows x 3 columns]

In [19]:

!mkdir assets

# Saving the sample submission in assets directory
test_df.to_csv(os.path.join("assets", "submission.csv"), index=False)

mkdir: cannot create directory ‘assets’: File exists


Mounting Google Drive 💾
Your Google Drive will be mounted to access the colab notebook
Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.activity.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fexperimentsandconfigs%20https%3a%2f%2fwww.googleapis.com%2fauth%2fphotos.native&response_type=code

Enter your authorization code:
